In [1]:
%pip install -q huggingface-hub plotly numpy

Note: you may need to restart the kernel to use updated packages.


In [ ]:
import plotly.graph_objects as go
import numpy as np

# Setting the time scale
time = np.arange(0, 24, 0.1)  # 24 hours, in increments of 0.1 hour

# Generating usage patterns
np.random.seed(42)
low_usage = (np.random.poisson(70, len(time)) * (np.random.rand(len(time)) < 0.15).astype(int))//2 
bursty_usage = np.random.poisson(70, len(time)) * (np.random.rand(len(time)) < 0.15).astype(int)
bursty_usage = np.random.poisson(100, len(time)) * (np.random.rand(len(time)) < 0.2).astype(int)//1.4

high_volume = np.random.normal(loc=15, scale=2, size=len(time))*1.75

# Applying smoothing
smooth_low_usage = np.convolve(low_usage, np.ones(50)/50, mode='same')
smooth_bursty_usage = np.convolve(bursty_usage, np.ones(50)/50, mode='same')
smooth_high_volume = np.convolve(high_volume, np.ones(50)/50, mode='same')
total_usage = smooth_low_usage + smooth_bursty_usage + smooth_high_volume

# Plotting using Plotly
fig = go.Figure()
fig.add_trace(go.Scatter(x=time, y=smooth_low_usage, mode='lines', name='Low Usage', line=dict(color='#B0C4DE')))  # Light Steel Blue
fig.add_trace(go.Scatter(x=time, y=smooth_bursty_usage, mode='lines', name='Bursty Usage', line=dict(color='#FFB6C1')))  # Light Pink
fig.add_trace(go.Scatter(x=time, y=smooth_high_volume, mode='lines', name='High Volume', line=dict(color='#98FB98')))  # Pale Green
fig.add_trace(go.Scatter(x=time, y=total_usage, mode='lines', name='Total Usage', line=dict(color='#2F4F4F', width=3)))  # Dark Slate Gray

fig.update_layout(
    title={
        'text': 'Comparison of Usage Models and Total Impact',
        'y': 0.9,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top',
        'font': {
            'size': 24  # Adjust the font size as needed
        }
    },
    xaxis_title='Time (hours)',
    yaxis_title='Requests',
    legend_title='Usage Pattern',
    xaxis=dict(
        title_font_size=28,  # Larger axis title font size
        tickfont_size=16  # Larger tick label font size
    ),
    yaxis=dict(
        title_font_size=28,  # Larger axis title font size
        tickfont_size=16  # Larger tick label font size
    ),
    legend=dict(
        x=0.5,  # Horizontal position, 0 is left
        y=-0.1,  # Vertical position, negative values to move it down
        orientation="h",  # Horizontal layout
        xanchor='center',  # Anchor the legend at the center
        yanchor='top'  # Anchor the legend at the top
    ),
    template='plotly_white'
)


fig.show()


# Push Image

In [ ]:
image_out = "multi-lora-serving-pattern.png"
fig.write_image(image_out, width=1920, height=1080, scale=2)

In [ ]:
from huggingface_hub import HfApi

api = HfApi()
api.upload_file(
    path_or_fileobj=image_out,
    path_in_repo=f"blog/multi-lora-serving/{image_out}",
    repo_id="huggingface/documentation-images",
    repo_type="dataset",
    commit_message="Updating title",
)

# Push Notebook

In [ ]:
from huggingface_hub import HfApi

api = HfApi()
api.upload_file(
    path_or_fileobj="multi-lora-serving-pattern.ipynb",
    path_in_repo="blog/multi-lora-serving/multi-lora-serving-pattern.ipynb",
    repo_id="huggingface/documentation-images",
    repo_type="dataset",
)